In [57]:
import pandas as pd
import numpy as np


In [58]:
# read data for fights and fighters
# bouts_clean = pd.read_csv("ufc_bouts_clean.csv")
# bouts_clean = pd.read_csv("bouts-morestats.csv")
bouts_clean = pd.read_csv("bouts_913.csv")


In [59]:
bouts_clean.tail()

Event            Date  \
7777          UFC 301: Pantoja vs. Erceg    May 04, 2024   
7778          UFC 301: Pantoja vs. Erceg    May 04, 2024   
7779  UFC Fight Night: Nicolau vs. Perez  April 27, 2024   
7780  UFC Fight Night: Nicolau vs. Perez  April 27, 2024   
7781  UFC Fight Night: Nicolau vs. Perez  April 27, 2024   

                                    Location W/L 1 W/L 2         Fighter 1  \
7777  Rio de Janeiro, Rio de Janeiro, Brazil   win   NaN     Dione Barbosa   
7778  Rio de Janeiro, Rio de Janeiro, Brazil   win   NaN  Myktybek Orolbai   
7779                  Las Vegas, Nevada, USA   win   NaN      Ketlen Souza   
7780                  Las Vegas, Nevada, USA   win   NaN    Don'Tale Mayes   
7781                  Las Vegas, Nevada, USA   win   NaN    Austin Hubbard   

               Fighter 2  Kd 1  Kd 2  Str 1  ...  Total str. 1 Total str. 2  \
7777  Ernesta Kareckaite     0     0     39  ...     87 of 124   100 of 220   
7778        Elves Brener     1     0     65  ...     79 of 125    83 of 138   
7779         Marnic Mann     0     0     80  ...    111 of 159    93 of 132   
7780        Caio Machado     1     0     67  ...     73 of 190    77 of 160   
7781       Michal Figlak     0     0     88  ...     99 of 220   100 of 218   

     Td % 1  Td % 2  Sub. att 1 Sub. att 2 Rev. 1  Rev. 2 Ctrl 1  Ctrl 2  
7777    18%    100%           1          0      1       3   3:51    3:25  
7778    50%     29%           0          0      2       0   2:55    7:12  
7779    40%     50%           1          0      1       1   2:54    3:11  
7780    ---     ---           0          0      0       0   0:36    0:00  
7781    42%      0%           0          0      0       0   0:48    1:37  

[5 rows x 35 columns]

In [61]:
unique_fighters = pd.unique(bouts_clean[['Fighter 1', 'Fighter 2']].values.ravel('K'))


In [62]:
more_fighter_stats = pd.read_csv("fighters_clean_0905.csv")


In [63]:
more_fighter_stats.head()


Name     Ht        Wt  Reach    Stance  Career W  Career L  \
0     Luiz Azeredo  5' 9"  154 lbs.     --  Orthodox        15        10   
1     Hunter Azure  5' 8"  145 lbs.  69.0"  Orthodox         9         2   
2        Tom Aaron     --  155 lbs.     --       NaN         5         3   
3  Luciano Azevedo  6' 3"  161 lbs.     --  Orthodox        17         9   
4    Marcos Galvao  5' 7"  135 lbs.     --  Orthodox        18         8   

            DOB born_year  
0  Jun 10, 1976      1976  
1  Mar 02, 1992      1992  
2  Jul 13, 1978      1978  
3  Jun 25, 1981      1981  
4  Jun 23, 1981      1981

In [64]:
# total = 0
# # Iterate over the DataFrame and print rows where 'born_year' is NaN or '--'
# for index, row in more_fighter_stats.iterrows():
#     if pd.isna(row['DOB']) or row['DOB'] == '--':
#         print(row)
#         total +=1
# print(total)
# print(more_fighter_stats.shape)


In [65]:
# Function to convert height to inches
def height_to_inches(height):
    try:
        # Split the height into feet and inches
        if pd.isna(height) or '--' in height:
            return None
        parts = height.split("' ")
        feet = int(parts[0])
        inches = int(parts[1].replace('"', ''))

        # Convert to total inches
        total_inches = feet * 12 + inches
        return total_inches
    except (ValueError, IndexError):
        return None

# Apply the function to the 'Ht' column
more_fighter_stats['Ht'] = more_fighter_stats['Ht'].apply(height_to_inches)


In [66]:
# Assuming 'Reach' is the name of your column
more_fighter_stats['Reach'] = more_fighter_stats['Reach'].str.replace('"', '', regex=False)


In [67]:
more_fighter_stats.drop("Wt", axis=1, inplace=True)


In [68]:
more_fighter_stats.drop("DOB", axis=1, inplace=True)


In [69]:
more_fighter_stats.head()


Name    Ht Reach    Stance  Career W  Career L born_year
0     Luiz Azeredo  69.0    --  Orthodox        15        10      1976
1     Hunter Azure  68.0  69.0  Orthodox         9         2      1992
2        Tom Aaron   NaN    --       NaN         5         3      1978
3  Luciano Azevedo  75.0    --  Orthodox        17         9      1981
4    Marcos Galvao  67.0    --  Orthodox        18         8      1981

In [70]:
more_fighter_stats.columns


Index(['Name', 'Ht', 'Reach', 'Stance', 'Career W', 'Career L', 'born_year'], dtype='object')

In [71]:
fighter_dfs = {}

for fighter in unique_fighters:
    # Filter rows where the fighter appears as either 'Fighter 1' or 'Fighter 2'
    fighter_df = bouts_clean[(bouts_clean['Fighter 1'] == fighter) | (bouts_clean['Fighter 2'] == fighter)].copy()

    # Remove rows where 'W/L 1' is 'NC'
    fighter_df = fighter_df[fighter_df['W/L 1'] != 'nc']

    # Identify the rows where the fighter is 'Fighter 2'
    is_fighter2 = fighter_df['Fighter 2'] == fighter

    # Swap columns for rows where the fighter is 'Fighter 2'
    columns_to_swap = ['W/L', 'Kd', 'Str', 'Td', 'Sub', 'KD', 'Sig. str.', 'Sig. str. %', 'Total str.', 'Td %', 'Sub. att', 'Rev.', 'Ctrl']

    for col in columns_to_swap:
        fighter_df.loc[is_fighter2, [f'{col} 1', f'{col} 2']] = fighter_df.loc[is_fighter2, [f'{col} 2', f'{col} 1']].values

    # Also swap 'Fighter 1' and 'Fighter 2' columns
    fighter_df.loc[is_fighter2, ['Fighter 1', 'Fighter 2']] = fighter_df.loc[is_fighter2, ['Fighter 2', 'Fighter 1']].values

    # Convert 'Date' column to datetime
    fighter_df['Date'] = pd.to_datetime(fighter_df['Date'], errors='coerce')

    # Sort the DataFrame by 'Date' column in ascending order
    fighter_df = fighter_df.sort_values(by='Date', ascending=True)

    # Reset the index to reflect the new order
    fighter_df = fighter_df.reset_index(drop=True)

    if fighter_df.empty:
        print(f"Deleting empty DataFrame for fighter: {fighter}")
    else:
        # Add additional columns from more_fighter_stats where 'Name' matches 'fighter'
        additional_stats = more_fighter_stats[more_fighter_stats['Name'] == fighter].drop(columns=['Name'])

        if not additional_stats.empty:
            for col in additional_stats.columns:
                fighter_df[col] = additional_stats.iloc[0][col]
        else:
            print(f"No additional stats found for fighter: {fighter}")

        # Store the updated DataFrame in the dictionary
        fighter_dfs[fighter] = fighter_df


Deleting empty DataFrame for fighter: Robert Drysdale
Deleting empty DataFrame for fighter: Mark Robinson
Deleting empty DataFrame for fighter: Ron Faircloth
Deleting empty DataFrame for fighter: Pedro Nobre
Deleting empty DataFrame for fighter: Hamdy Abdelwahab


In [72]:
fighter_dfs['Dustin Poirier']


Event       Date  \
0                                 UFC 125: Resolution 2011-01-01   
1                       UFC 131: Dos Santos vs Carwin 2011-06-11   
2                 UFC on FOX: Velasquez vs Dos Santos 2011-11-12   
3                             UFC 143: Diaz vs Condit 2012-02-04   
4            UFC on FUEL TV: Korean Zombie vs Poirier 2012-05-15   
5   The Ultimate Fighter: Team Carwin vs. Team Nel... 2012-12-15   
6                   UFC on FUEL TV: Barao vs McDonald 2013-02-16   
7                      UFC 164: Henderson vs Pettis 2 2013-08-31   
8                         UFC 168: Weidman vs Silva 2 2013-12-28   
9                 UFC Fight Night: Bisping vs Kennedy 2014-04-16   
10                        UFC 178: Johnson vs Cariaso 2014-09-27   
11                   UFC Fight Night: Mendes vs Lamas 2015-04-04   
12              UFC Fight Night: Boetsch vs Henderson 2015-06-06   
13                          UFC 195: Lawler vs Condit 2016-01-02   
14                    UFC 199: Rockhold vs. Bisping 2 2016-06-04   
15               UFC Fight Night: Poirier vs. Johnson 2016-09-17   
16                      UFC 208: Holm vs. De Randamie 2017-02-11   
17                UFC Fight Night: Poirier vs. Pettis 2017-11-11   
18               UFC Fight Night: Poirier vs. Gaethje 2018-04-14   
19             UFC Fight Night: Alvarez vs. Poirier 2 2018-07-28   
20                    UFC 236: Holloway vs. Poirier 2 2019-04-13   
21                        UFC 242: Khabib vs. Poirier 2019-09-07   
22                UFC Fight Night: Poirier vs. Hooker 2020-06-27   
23                      UFC 257: Poirier vs. McGregor 2021-01-23   
24                    UFC 264: Poirier vs. McGregor 3 2021-07-10   
25                      UFC 269: Oliveira vs. Poirier 2021-12-11   
26                      UFC 281: Adesanya vs. Pereira 2022-11-12   
27                     UFC 291: Poirier vs. Gaethje 2 2023-07-29   
28                       UFC 299: O'Malley vs. Vera 2 2024-03-09   
29                     UFC 302: Makhachev vs. Poirier 2024-06-01   

                                      Location W/L 1 W/L 2       Fighter 1  \
0                       Las Vegas, Nevada, USA   win   NaN  Dustin Poirier   
1          Vancouver, British Columbia, Canada   win   NaN  Dustin Poirier   
2                     Anaheim, California, USA   win   NaN  Dustin Poirier   
3                       Las Vegas, Nevada, USA   win   NaN  Dustin Poirier   
4                       Fairfax, Virginia, USA   NaN   win  Dustin Poirier   
5                       Las Vegas, Nevada, USA   win   NaN  Dustin Poirier   
6              London, England, United Kingdom   NaN   win  Dustin Poirier   
7                    Milwaukee, Wisconsin, USA   win   NaN  Dustin Poirier   
8                       Las Vegas, Nevada, USA   win   NaN  Dustin Poirier   
9                  Quebec City, Quebec, Canada   win   NaN  Dustin Poirier   
10                      Las Vegas, Nevada, USA   NaN   win  Dustin Poirier   
11                      Fairfax, Virginia, USA   win   NaN  Dustin Poirier   
12                 New Orleans, Louisiana, USA   win   NaN  Dustin Poirier   
13                      Las Vegas, Nevada, USA   win   NaN  Dustin Poirier   
14                Los Angeles, California, USA   win   NaN  Dustin Poirier   
15                         Hidalgo, Texas, USA   NaN   win  Dustin Poirier   
16                     Brooklyn, New York, USA   win   NaN  Dustin Poirier   
17                      Norfolk, Virginia, USA   win   NaN  Dustin Poirier   
18                      Glendale, Arizona, USA   win   NaN  Dustin Poirier   
19                    Calgary, Alberta, Canada   win   NaN  Dustin Poirier   
20                       Atlanta, Georgia, USA   win   NaN  Dustin Poirier   
21  Abu Dhabi, Abu Dhabi, United Arab Emirates   NaN   win  Dustin Poirier   
22                      Las Vegas, Nevada, USA   win   NaN  Dustin Poirier   
23  Abu Dhabi, Abu Dhabi, United Arab Emirates   win   NaN  Dustin 

In [73]:
for fighter in fighter_dfs:
    fighter_df = fighter_dfs[fighter]

    # Initialize W, L, Num Fights, and W Perc columns using .loc
    fighter_df.loc[:, 'W'] = 0
    fighter_df.loc[:, 'L'] = 0
    fighter_df.loc[:, 'Num Fights'] = 0
    fighter_df.loc[:, 'W Perc'] = 0

    # Initialize Sig Str columns for totals and percentages
    fighter_df.loc[:, 'Sig Strikes Avg'] = 0
    # fighter_df.loc[:, 'Sig Attempts 1'] = 0
    fighter_df.loc[:, 'Sig Str %'] = 0.0

    fighter_df.loc[:, 'Sig Strikes Opp Avg'] = 0
    # fighter_df.loc[:, 'Sig Attempts 2'] = 0
    fighter_df.loc[:, 'Sig Str % Opp'] = 0.0

    # Initialize Total Str columns for totals and percentages
    fighter_df.loc[:, 'Strikes Avg'] = 0
    # fighter_df.loc[:, 'Strike Attempts 1'] = 0
    fighter_df.loc[:, 'Str %'] = 0.0

    fighter_df.loc[:, 'Strikes Opp Avg'] = 0
    # fighter_df.loc[:, 'Strike Attempts 2'] = 0
    fighter_df.loc[:, 'Str % Opp'] = 0.0

    # Initialize TD columns for totals and percentages
    fighter_df.loc[:, 'TD Avg'] = 0
    # fighter_df.loc[:, 'Strike Attempts 1'] = 0
    fighter_df.loc[:, 'TD %'] = 0.0

    fighter_df.loc[:, 'TD Opp Avg'] = 0
    # fighter_df.loc[:, 'Strike Attempts 2'] = 0
    fighter_df.loc[:, 'TD % Opp'] = 0.0

    # Initialize KD Total columns for running count of knockdowns
    fighter_df.loc[:, 'KD Avg'] = 0
    fighter_df.loc[:, 'KD Opp Avg'] = 0

    # Initialize Method columns for DEC and KO counts
    fighter_df.loc[:, 'DEC Avg'] = 0
    fighter_df.loc[:, 'KO Avg'] = 0
    fighter_df.loc[:, 'SUB Avg'] = 0
    fighter_df.loc[:, 'DEC Opp Avg'] = 0
    fighter_df.loc[:, 'KO Opp Avg'] = 0
    fighter_df.loc[:, 'SUB Opp Avg'] = 0

    # Initialize the new columns with 0 for the first row
    fighter_df['CTRL Avg'] = 0
    fighter_df['CTRL Opp Avg'] = 0
    fighter_df['Time Avg'] = 0

    # Add a new column for streak
    fighter_df['Streak'] = 0

    # Add new column for Ht diff
    fighter_df['Ht Diff'] = 0

    # Add new column for Reach diff
    fighter_df['Reach Diff'] = 0

    # Add new column for Age
    fighter_df['Age'] = 0

    # Iterate through rows to update W/L records and other metrics
    wins = 0
    losses = 0
    fights = 0
    w_perc = 0

    # Initialize running totals for Sig Str
    running_sig_strikes_1 = 0
    running_attempted_strikes_1 = 0
    running_sig_strikes_2 = 0
    running_attempted_strikes_2 = 0

    # Initialize running totals for Total Str
    running_strikes_1 = 0
    running_attempted_strikes_1 = 0
    running_strikes_2 = 0
    running_attempted_strikes_2 = 0

    # Initialize running totals for Total TD
    running_td_1 = 0
    running_attempted_td_1 = 0
    running_td_2 = 0
    running_attempted_td_2 = 0

    # Initialize running totals for Submissions
    running_submissions_1 = 0
    running_submissions_2 = 0

    # Initialize running totals for KD
    running_kd_1 = 0
    running_kd_2 = 0

    # Initialize running totals for Method DEC and KO and SUB
    running_dec = 0
    running_ko = 0
    running_sub = 0
    running_dec_opp = 0
    running_ko_opp = 0
    running_sub_opp = 0

    # Initialize running totals
    running_ctrl_1 = 0
    running_ctrl_2 = 0
    running_time = 0

    # Initialize streak
    streak = 0

    # Initialize career wins, losses
    career_w = fighter_df['Career W'].values[len(fighter_df) -1 ]
    career_l = fighter_df['Career L'].values[len(fighter_df) -1 ]

    for i in range(len(fighter_df)):
        # Get the opponent's stats
        opponent = fighter_df.iloc[i]['Fighter 2']
        opponent_row = more_fighter_stats.loc[more_fighter_stats['Name'] == opponent]
        if not opponent_row.empty:
            # Get opponent's height and fighter's height as scalar values
            opponent_ht = opponent_row['Ht'].values[0] if not opponent_row['Ht'].isna().all() else np.nan
            ht = fighter_df.iloc[i]['Ht'] if not pd.isna(fighter_df.iloc[i]['Ht']) else np.nan
            # Check for NaN using np.isnan()
            if not np.isnan(opponent_ht) and not np.isnan(ht):
                fighter_df.loc[fighter_df.index[i], 'Ht Diff'] = ht - opponent_ht
            else:
                print(f"Empty value for height for fighter: {fighter}")

            #Reach
            # Get opponent's reach and fighter's reach as scalar values
            opponent_reach = opponent_row['Reach'].values[0] if not opponent_row['Reach'].isna().all() else '--'
            reach = fighter_df.iloc[i]['Reach'] if not pd.isna(fighter_df.iloc[i]['Reach']) else '--'
            # Compare the values
            if opponent_reach != '--' and reach != '--':
                fighter_df.loc[fighter_df.index[i], 'Reach Diff'] = float(reach) - float(opponent_reach)
            else:
                fighter_df.loc[fighter_df.index[i], 'Reach Diff'] = 0

        # Get Age
        birth_year = fighter_df.iloc[i]['born_year']
        date = fighter_df.iloc[i]['Date']
        # Extract the year from the Timestamp
        year = date.year if not pd.isna(date) else None

        if birth_year != '--':
            fighter_df.loc[fighter_df.index[i], 'Age'] = int(year) - int(birth_year)
        else:
            fighter_df.loc[fighter_df.index[i], 'Age'] = 0

        # Check the result of the fight (assuming 'W/L 1' indicates the result for Fighter 1)
        if i != 0:
            if fighter_df.iloc[i-1]['W/L 1'] == 'win':
                if streak < 0:
                    streak = 1
                else:
                    streak += 1
            else:
                if streak > 0:
                    streak = -1
                else:
                    streak -= 1

            # Update the streak column
            fighter_df.loc[fighter_df.index[i], 'Streak'] = streak

        if fighter_df.iloc[len(fighter_df) - 1 - i]['W/L 1']=='win':
            career_w -= 1
        else:
            career_l -= 1

        fighter_df.loc[fighter_df.index[len(fighter_df) - 1 - i], 'Career W'] = career_w
        fighter_df.loc[fighter_df.index[len(fighter_df) - 1 - i], 'Career L'] = career_l
        fighter_df.loc[fighter_df.index[len(fighter_df) - 1 - i], 'Career Fights'] = career_l + career_w
        if career_l + career_w != 0:
            fighter_df.loc[fighter_df.index[len(fighter_df) - 1 - i], 'Career W Perc'] = career_w / (career_l + career_w) * 100
        else:
            fighter_df.loc[fighter_df.index[len(fighter_df) - 1 - i], 'Career W Perc'] = 0

        if i == (len(fighter_df) - 1):
            continue

        ### Update for W, L, Num Fights, and W Perc
        result = fighter_df.iloc[i]['W/L 1']  # Assuming 'W/L 1' is the column that has 'W', 'L', or 'NC'
        # Skip the record if the result is 'NC'
        if result != 'nc':
            if fighter_df.iloc[i]['W/L 1'] == 'win':
                wins += 1
            else:
                losses += 1
            fights += 1
            w_perc = wins / fights
        fighter_df.loc[fighter_df.index[i + 1], 'W'] = wins
        fighter_df.loc[fighter_df.index[i + 1], 'L'] = losses
        fighter_df.loc[fighter_df.index[i + 1], 'Num Fights'] = fights
        fighter_df.loc[fighter_df.index[i + 1], 'W Perc'] = int(w_perc * 100.0)

        # Update control time and total time based on existing columns
        for string in ['Ctrl 1', 'Ctrl 2', 'Time']:
            time_str = fighter_df.iloc[i][string]
            if ':' in time_str:
                minutes, seconds = map(int, time_str.split(':'))
                total_seconds = minutes * 60 + seconds
                if string == 'Time':
                    total_seconds += (fighter_df.iloc[i]['Round'] - 1) * 300
                fighter_df.loc[fighter_df.index[i], string] = total_seconds
            else:
                fighter_df.loc[fighter_df.index[i], string] = 0

        # Update running totals for 'CTRL Total' and 'Time Total'
        if 'Ctrl 1' in fighter_df.columns:
            running_ctrl_1 += fighter_df.iloc[i]['Ctrl 1']
        if 'Ctrl 2' in fighter_df.columns:
            running_ctrl_2 += fighter_df.iloc[i]['Ctrl 2']
        if 'Time' in fighter_df.columns:
            running_time += fighter_df.iloc[i]['Time']

        # Assign running totals to new columns
        fighter_df.loc[fighter_df.index[i+1], 'CTRL Avg'] = 0.0 if fights==0 else running_ctrl_1/fights
        fighter_df.loc[fighter_df.index[i+1], 'CTRL Opp Avg'] = 0.0 if fights==0 else running_ctrl_2/fights
        fighter_df.loc[fighter_df.index[i+1], 'Time Avg'] = 0.0 if fights==0 else running_time/fights

        ### Update for Sig Str 1 totals and running career sig str %
        for j, sig_str_col in enumerate(['Sig. str. 1', 'Sig. str. 2'], start=1):
            sig_str_value = fighter_df.iloc[i][sig_str_col]
            strikes, attempts = map(int, sig_str_value.split(' of '))

            if j == 1:
                running_sig_strikes_1 += strikes
                running_attempted_strikes_1 += attempts
                if running_attempted_strikes_1 == 0:
                    sig_str_percentage_1 = 0
                else:
                    sig_str_percentage_1 = (running_sig_strikes_1 / running_attempted_strikes_1) * 100

                fighter_df.loc[fighter_df.index[i + 1], 'Sig Strikes Avg'] = 0.0 if fights==0 else running_sig_strikes_1/fights
                # fighter_df.loc[fighter_df.index[i + 1], 'Sig Attempts 1'] = running_attempted_strikes_1
                fighter_df.loc[fighter_df.index[i + 1], 'Sig Str %'] = sig_str_percentage_1

            elif j == 2:
                running_sig_strikes_2 += strikes
                running_attempted_strikes_2 += attempts
                if running_attempted_strikes_2 == 0:
                    sig_str_percentage_2 = 0
                else:
                    sig_str_percentage_2 = (running_sig_strikes_2 / running_attempted_strikes_2) * 100

                fighter_df.loc[fighter_df.index[i + 1], 'Sig Strikes Opp Avg'] = 0.0 if fights==0 else running_sig_strikes_2/fights
                # fighter_df.loc[fighter_df.index[i + 1], 'Sig Attempts 2'] = running_attempted_strikes_2
                fighter_df.loc[fighter_df.index[i + 1], 'Sig Str % Opp'] = sig_str_percentage_2

        ## Update for Total Str (Strikes 1 and Strikes 2)
        for j, total_str_col in enumerate(['Total str. 1', 'Total str. 2'], start=1):
            total_str_value = fighter_df.iloc[i][total_str_col]
            strikes, attempts = map(int, total_str_value.split(' of '))

            if j == 1:
                running_strikes_1 += strikes
                running_attempted_strikes_1 += attempts
                if running_attempted_strikes_1 == 0:
                    str_percentage_1 = 0
                else:
                    str_percentage_1 = (running_strikes_1 / running_attempted_strikes_1) * 100

                fighter_df.loc[fighter_df.index[i + 1], 'Strikes Avg'] = 0.0 if fights==0 else running_strikes_1/fights
                # fighter_df.loc[fighter_df.index[i + 1], 'Strike Attempts 1'] = running_attempted_strikes_1
                fighter_df.loc[fighter_df.index[i + 1], 'Str %'] = str_percentage_1

            elif j == 2:
                running_strikes_2 += strikes
                running_attempted_strikes_2 += attempts
                if running_attempted_strikes_2 == 0:
                    str_percentage_2 = 0
                else:
                    str_percentage_2 = (running_strikes_2 / running_attempted_strikes_2) * 100

                fighter_df.loc[fighter_df.index[i + 1], 'Strikes Opp Avg'] = 0.0 if fights==0 else running_strikes_2/fights
                # fighter_df.loc[fighter_df.index[i + 1], 'Strike Attempts 2'] = running_attempted_strikes_2
                fighter_df.loc[fighter_df.index[i + 1], 'Str % Opp'] = str_percentage_2

        ## Update for Total Str (Strikes 1 and Strikes 2)
        for j, td_str_col in enumerate(['Td 1', 'Td 2'], start=1):
            td_str = fighter_df.iloc[i][td_str_col]
            td, attempts = map(int, td_str.split(' of '))

            if j == 1:
                running_td_1 += td
                running_attempted_td_1 += attempts
                if running_attempted_td_1 == 0:
                    td_percentage_1 = 0
                else:
                    td_percentage_1 = (running_td_1 / running_attempted_td_1) * 100

                fighter_df.loc[fighter_df.index[i + 1], 'TD Avg'] = 0.0 if fights==0 else running_td_1/fights
                # fighter_df.loc[fighter_df.index[i + 1], 'TD Attempts 1'] = running_attempted_td_1
                fighter_df.loc[fighter_df.index[i + 1], 'TD %'] = td_percentage_1

            elif j == 2:
                running_td_2 += td
                running_attempted_td_2 += attempts
                if running_attempted_td_2 == 0:
                    td_percentage_2 = 0
                else:
                    td_percentage_2 = (running_td_2 / running_attempted_td_2) * 100

                fighter_df.loc[fighter_df.index[i + 1], 'TD Opp Avg'] = 0.0 if fights==0 else running_td_2/fights
                # fighter_df.loc[fighter_df.index[i + 1], 'TD Attempts 2'] = running_attempted_td_2
                fighter_df.loc[fighter_df.index[i + 1], 'TD % Opp'] = td_percentage_2

        ### Update for Sub Total 1 and Sub Total 2
        for j, kd_col in enumerate(['KD 1', 'KD 2'], start=1):
            kd = fighter_df.iloc[i][kd_col]

            if j == 1:
                running_kd_1 += kd
                fighter_df.loc[fighter_df.index[i + 1], 'KD Avg'] = 0.0 if fights==0 else running_kd_1/fights

            elif j == 2:
                running_kd_2 += kd
                fighter_df.loc[fighter_df.index[i + 1], 'KD Opp Avg'] = 0.0 if fights==0 else running_kd_2/fights

        ### Update for Method DEC and KO
        method = fighter_df.iloc[i]['Method']
        if 'DEC' in method:
            if fighter_df.iloc[i]['W/L 1'] == 'win':
                running_dec += 1
            else:
                running_dec_opp += 1
        if 'KO' in method:
            if fighter_df.iloc[i]['W/L 1'] == 'win':
                running_ko += 1
            else:
                running_ko_opp += 1
        if 'SUB' in method:
            if fighter_df.iloc[i]['W/L 1'] == 'win':
                running_sub += 1
            else:
                running_sub_opp += 1

        fighter_df.loc[fighter_df.index[i + 1], 'DEC Avg'] = 0.0 if fights==0 else running_dec/fights
        fighter_df.loc[fighter_df.index[i + 1], 'DEC Opp Avg'] = 0.0 if fights==0 else running_dec_opp/fights
        fighter_df.loc[fighter_df.index[i + 1], 'KO Avg'] = 0.0 if fights==0 else running_ko/fights
        fighter_df.loc[fighter_df.index[i + 1], 'KO Opp Avg'] = 0.0 if fights==0 else running_ko_opp/fights
        fighter_df.loc[fighter_df.index[i + 1], 'SUB Avg'] = 0.0 if fights==0 else running_sub/fights
        fighter_df.loc[fighter_df.index[i + 1], 'SUB Opp Avg'] = 0.0 if fights==0 else running_sub_opp/fights

    # Remove the specified columns
    fighter_df = fighter_df.drop(columns=[
        'Sig. str. 1', 'Sig. str. 2', 'Sig. str. % 1', 'Sig. str. % 2',
        'Total str. 1', 'Total str. 2', 'W/L 2', 'Rev. 1', 'Rev. 2', 'Sub. att 1',
        'Sub. att 2', 'Sub 1', 'Sub 2', 'Str 1', 'Str 2', 'Td % 1', 'Td % 2',
        'Td 1', 'Td 2', 'Kd 1', 'Kd 2', 'Method', 'Round', 'Ctrl 1', 'Ctrl 2', 'Time',
        'KD 1', 'KD 2', 'Ht', 'Reach'
    ])

    fighter_dfs[fighter] = fighter_df


/tmp/ipykernel_6739/2498811324.py:222: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise in a future error of pandas. Value '383.5' has dtype incompatible with int64, please explicitly cast to a compatible dtype first.
  fighter_df.loc[fighter_df.index[i+1], 'CTRL Opp Avg'] = 0.0 if fights==0 else running_ctrl_2/fights
/tmp/ipykernel_6739/2498811324.py:238: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise in a future error of pandas. Value '63.5' has dtype incompatible with int64, please explicitly cast to a compatible dtype first.
  fighter_df.loc[fighter_df.index[i + 1], 'Sig Strikes Avg'] = 0.0 if fights==0 else running_sig_strikes_1/fights
/tmp/ipykernel_6739/2498811324.py:250: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise in a future error of pandas. Value '65.5' has dtype incompatible with int64, please explicitly cast to a compatible dtype first.
  fighter_df.loc[fighter_df.index

In [74]:
# 'DEC', 'KO',
#        'SUB', 'DEC Opp', 'KO Opp', 'SUB Opp',

# 'Sig Strikes',
#'Sig Strikes Opp',
# 'Strikes'
# 'Strikes Opp',
# 'TD',
# 'TD Opp',
# 'KD Total', 'KD Total Opp',
# 'CTRL Total', 'CTRL Total Opp',
# 'Time Total'


In [75]:
fighter_dfs['Conor McGregor'].columns


Index(['Event', 'Date', 'Location', 'W/L 1', 'Fighter 1', 'Fighter 2',
       'Weight class', 'Stance', 'Career W', 'Career L', 'born_year', 'W', 'L',
       'Num Fights', 'W Perc', 'Sig Strikes Avg', 'Sig Str %',
       'Sig Strikes Opp Avg', 'Sig Str % Opp', 'Strikes Avg', 'Str %',
       'Strikes Opp Avg', 'Str % Opp', 'TD Avg', 'TD %', 'TD Opp Avg',
       'TD % Opp', 'KD Avg', 'KD Opp Avg', 'DEC Avg', 'KO Avg', 'SUB Avg',
       'DEC Opp Avg', 'KO Opp Avg', 'SUB Opp Avg', 'CTRL Avg', 'CTRL Opp Avg',
       'Time Avg', 'Streak', 'Ht Diff', 'Reach Diff', 'Age', 'Career Fights',
       'Career W Perc'],
      dtype='object')

In [76]:
import pandas as pd

# Initialize an empty list to collect all the DataFrames
all_fights_list = []

# Iterate over the dictionary of fighter DataFrames
for fighter, fighter_df in fighter_dfs.items():
    # Append the fighter's DataFrame to the list
    all_fights_list.append(fighter_df)

# Concatenate all the DataFrames in the list into one large DataFrame
all_fights_combined = pd.concat(all_fights_list, ignore_index=True)

# Optionally, drop any duplicate rows to ensure each fight is only listed once
all_fights_combined = all_fights_combined.drop_duplicates()

# Now, `all_fights_combined` contains the consolidated data with all the new stats


In [77]:
# rows_mine = all_fights_combined[all_fights_combined['Event'] == 'UFC Fight Night: Blaydes vs. Aspinall']
# rows_fight = rows_mine[(rows_mine['Fighter 1'] == 'Charles Johnson') | (rows_mine['Fighter 2'] == 'Charles Johnson')]
# print(rows_fight)
all_fights_combined


Event       Date  \
0        UFC Fight Night: Blaydes vs. Aspinall 2022-07-23   
1      UFC Fight Night: Nzechukwu vs. Cutelaba 2022-11-19   
2       UFC Fight Night: Strickland vs. Imavov 2023-01-14   
3             UFC Fight Night: Muniz vs. Allen 2023-02-25   
4              UFC Fight Night: Song vs. Simon 2023-04-29   
...                                        ...        ...   
15387       UFC 297: Strickland vs. Du Plessis 2024-01-20   
15388       UFC Fight Night: Nicolau vs. Perez 2024-04-27   
15389      UFC Fight Night: Allen vs. Curtis 2 2024-04-06   
15390      UFC Fight Night: Allen vs. Curtis 2 2024-04-06   
15391               UFC 301: Pantoja vs. Erceg 2024-05-04   

                                     Location W/L 1           Fighter 1  \
0             London, England, United Kingdom   NaN     Charles Johnson   
1                      Las Vegas, Nevada, USA   win     Charles Johnson   
2                      Las Vegas, Nevada, USA   win     Charles Johnson   
3                      Las Vegas, Nevada, USA   NaN     Charles Johnson   
4                      Las Vegas, Nevada, USA   NaN     Charles Johnson   
...                                       ...   ...                 ...   
15387                Toronto, Ontario, Canada   NaN        Serhiy Sidey   
15388                  Las Vegas, Nevada, USA   NaN       James Llontop   
15389                  Las Vegas, Nevada, USA   NaN        Pedro Falcao   
15390                  Las Vegas, Nevada, USA   NaN         Dylan Budka   
15391  Rio de Janeiro, Rio de Janeiro, Brazil   NaN  Ernesta Kareckaite   

                Fighter 2       Weight class    Stance  Career W  Career L  \
0         Muhammad Mokaev          Flyweight    Switch        11         2   
1      Zhalgas Zhumagulov          Flyweight    Switch        11         3   
2             Jimmy Flick          Flyweight    Switch        12         3   
3            Ode Osbourne       Catch Weight    Switch        13         3   
4             Cody Durden          Flyweight    Switch        13         4   
...                   ...                ...       ...       ...       ...   
15387       Ramon Taveras       Bantamweight    Switch        10         1   
15388       Chris Padilla        Lightweight  Orthodox        14         3   
15389         Victor Hugo       Bantamweight  Orthodox        16         3   
15390       Cesar Almeida       Middleweight    Switch         7         2   
15391       Dione Barbosa  Women's Flyweight  Orthodox         5         0   

       ... SUB Opp Avg  CTRL Avg  CTRL Opp Avg  Time Avg  Streak  Ht Diff  \
0      ...         0.0      0.00      0.000000      0.00       0        2   
1      ...         0.0     27.00    704.000000    900.00      -1        5   
2      ...         0.0     42.00    383.500000    900.00       1        2   
3      ...         0.0     61.00    263.666667    691.00       2        2   
4      ...         0.0     65.25    241.000000    743.25      -1        2   
...    ...         ...       ...           ...       ...     ...      ...   
15387  ...         0.0      0.00      0.000000      0.00       0        3   
15388  ...         0.0      0.00      0.000000      0.00       0        3   
15389  ...         0.0      0.00      0.000000      0.00       0       -1   
15390  ...         0.0      0.00      0.000000      0.00       0       -1   
15391  ...         0.0      0.00      0.000000      0.00       0        3   

       Reach Diff  Age  Career Fights  Career W Perc  
0               0   31           13.0      84.615385  
1               4   31           14.0      78.571429  
2               2   32           15.0      80.000000  
3              -3   32           16.0      81.250000  
4               3   32           17.0      76.470588  
...           ...  ...            ...            ...  
15387           2   28           11.0      90.909091  
15388          -1   25           17.0      82.352941  
15389          -5   32           19.0      84.2105

In [79]:
# List of unique stats
unique_stats = ['W', 'L', 'Num Fights', 'W Perc', 'Sig Strikes Avg', 'Sig Str %',
                'Sig Strikes Opp Avg', 'Sig Str % Opp', 'Strikes Avg', 'Str %',
                'Strikes Opp Avg', 'Str % Opp', 'TD Avg', 'TD %', 'TD Opp Avg',
                'TD % Opp', 'KD Avg', 'KD Opp Avg', 'DEC Avg', 'KO Avg',
                'SUB Avg', 'DEC Opp Avg', 'KO Opp Avg', 'SUB Opp Avg', 'CTRL Avg',
                'CTRL Opp Avg', 'Time Avg', 'Streak', 'Career W', 'Career L', 'Career Fights', 'Career W Perc',
                'Ht Diff', 'Reach Diff', 'Age', 'Stance','born_year']

# Create a new DataFrame to store combined rows
combined_df = pd.DataFrame()

# Track processed indices to avoid re-processing
processed_indices = set()

# Iterate over each row to find and combine matching rows
for idx, row1 in all_fights_combined.iterrows():
    # Skip if this row has already been processed
    if idx in processed_indices:
        continue

    # Find the matching row where Fighter 1 and Fighter 2 are swapped
    matching_row = all_fights_combined[
        (all_fights_combined['Event'] == row1['Event']) &
        (all_fights_combined['Fighter 1'] == row1['Fighter 2']) &
        (all_fights_combined['Fighter 2'] == row1['Fighter 1'])
    ]

    if not matching_row.empty:
        row2 = matching_row.iloc[0]
        row2_idx = matching_row.index[0]

        # Combine rows, giving '1' suffix to row1 stats and '2' suffix to row2 stats
        combined_row = row1.copy()

        # Update stats with '2' suffix from the second row
        for stat in unique_stats:
            combined_row[stat + ' 2'] = row2[stat]

        # Rename original stats to '1' suffix for consistency
        for stat in unique_stats:
            combined_row.rename({stat: stat + ' 1'}, inplace=True)

        # Add combined row to the new DataFrame
        combined_df = pd.concat([combined_df, combined_row.to_frame().T], ignore_index=True)

        # Add the indices of processed rows to avoid duplication
        processed_indices.add(idx)
        processed_indices.add(row2_idx)

# Reset index for the final combined DataFrame
combined_df.reset_index(drop=True, inplace=True)

# Display the combined DataFrame
print(combined_df.head())


                                     Event                 Date  \
0    UFC Fight Night: Blaydes vs. Aspinall  2022-07-23 00:00:00   
1  UFC Fight Night: Nzechukwu vs. Cutelaba  2022-11-19 00:00:00   
2   UFC Fight Night: Strickland vs. Imavov  2023-01-14 00:00:00   
3         UFC Fight Night: Muniz vs. Allen  2023-02-25 00:00:00   
4          UFC Fight Night: Song vs. Simon  2023-04-29 00:00:00   

                          Location W/L 1        Fighter 1           Fighter 2  \
0  London, England, United Kingdom   NaN  Charles Johnson     Muhammad Mokaev   
1           Las Vegas, Nevada, USA   win  Charles Johnson  Zhalgas Zhumagulov   
2           Las Vegas, Nevada, USA   win  Charles Johnson         Jimmy Flick   
3           Las Vegas, Nevada, USA   NaN  Charles Johnson        Ode Osbourne   
4           Las Vegas, Nevada, USA   NaN  Charles Johnson         Cody Durden   

   Weight class Stance 1 Career W 1 Career L 1  ... Streak 2 Career W 2  \
0     Flyweight   Switch         11

In [ ]:
# Create a new DataFrame with rows where 'Career W Perc 1' is NaN
# nan_rows_df = combined_df[combined_df['Ht 1'].isna()]

# # Display the new DataFrame with NaN rows
# print(nan_rows_df['Fighter 1'])


Series([], Name: Fighter 1, dtype: object)


In [ ]:
# Create a new DataFrame with rows where 'Career W Perc 1' is NaN
# nan_rows_df = combined_df[combined_df['Reach 2']=='--']

# # Display the new DataFrame with NaN rows
# print(nan_rows_df['Fighter 2'].unique())


['Justin Wren' 'Maiquel Falcao' 'Alan Omer' 'Chase Gormley'
 'Jason Thacker' 'Edwin DeWees' 'Jake Rosholt' 'Jay Silva' 'Ben Earwood'
 'Tiki Ghosn' 'Ronald Jhun' 'Jason Gilliam' 'Chris Price' 'Sam Hoger'
 'Mike Nickels' 'Delson Heleno' 'CJ Keith' 'Motonobu Tezuka' 'Alberto Uda'
 'Billy Miles' 'Roman Mitichyan' 'Ronys Torres' 'Antonio McKee'
 'Jorge Lopez' 'David Baron' 'Steve Lopez' 'Dashon Johnson'
 'Ian Entwistle' 'Leo Kuntz' 'Marcin Wrzosek' 'Charlie Ward'
 'Julio Paulino' 'Amilcar Alves' 'Paul Bradley' 'Emily Kagan' 'Rocky Lee'
 'Jay Cucciniello' 'Juan Manuel Puig' 'Jack May' 'Guto Inocente'
 'Sean Daugherty' 'Patrick Smith' 'Ray Wizard' 'Royce Gracie'
 'Johnny Rhodes' 'Rudyard Moncayo' 'John Matua' 'Paul Varelans'
 'Oleg Taktarov' 'Steve Jennum' 'Dan Severn' 'Sam Adkins' 'Scott Ferrozzo'
 'Don Frye' 'Cal Worsham' 'Steve Nelmark' 'Maurice Smith' 'Yoji Anjo'
 'Hugo Duarte' 'Pedro Rizzo' 'Kimo Leopoldo' 'Wesley Correira'
 'Minoki Ichihara' 'Remco Pardoel' 'Jason DeLucia' 'Ron van Clie

In [80]:
combined_df[combined_df['Fighter 1']=='Frank Hamaker']


Event                 Date               Location W/L 1  \
1626  UFC 2: No Way Out  1994-03-11 00:00:00  Denver, Colorado, USA   win   

          Fighter 1        Fighter 2 Weight class Stance 1 Career W 1  \
1626  Frank Hamaker  Thaddeus Luster  Open Weight      NaN          0   

     Career L 1  ... Streak 2 Career W 2 Career L 2 Career Fights 2  \
1626          0  ...        0          0          0             0.0   

     Career W Perc 2 Ht Diff 2 Reach Diff 2 Age 2 Stance 2 born_year 2  
1626             0.0         1            0     0      NaN          --  

[1 rows x 81 columns]

In [81]:
combined_df['Stance 1'] = combined_df['Stance 1'].replace({np.nan: None})
combined_df['Stance 2'] = combined_df['Stance 2'].replace({np.nan: None})


In [85]:
df_nan_stance = combined_df[(combined_df['Stance 1'].isna()) | (combined_df['Stance 2'].isna())]


In [86]:
print(df_nan_stance)


                                                  Event                 Date  \
931   The Ultimate Fighter: Team McGregor vs. Team F...  2015-12-11 00:00:00   
1004  The Ultimate Fighter: A Champion Will Be Crown...  2014-12-12 00:00:00   
1497                                  UFC 2: No Way Out  1994-03-11 00:00:00   
1499                                  UFC 2: No Way Out  1994-03-11 00:00:00   
1530                     UFC 5: The Return of the Beast  1995-04-07 00:00:00   
...                                                 ...                  ...   
6318                 UFC on FOX: Dos Anjos vs. Cowboy 2  2015-12-19 00:00:00   
6331                  UFC Fight Night: Silva vs Bisping  2016-02-27 00:00:00   
6381             UFC Fight Night: Rodriguez vs. Caceres  2016-08-06 00:00:00   
6871  The Ultimate Fighter: A New World Champion Finale  2017-12-01 00:00:00   
7671               UFC Fight Night: Ribas vs. Namajunas  2024-03-23 00:00:00   

                             Location W

In [ ]:
# 1626     Frank Hamaker 6 2
# 1710       Jack Nilson 6 3
# 1896    Tulio Palhares 5 10
# 1040      Edward Faaloloto 5 9
# 1499            Ray Wizard 5 10
# 1554            John Dowdy 6 2
# 1571    Felix Lee Mitchell 5 11
# 1695            Sam Fulton 6 2
# 1710        Saeed Hosseini 6 4
# 1804         Noe Hernandez 5 10
# 1896        Adriano Santos 5 10
# 1928         Frank Caracci 5 7
# 3166      Edward Faaloloto 5 9
# 4051        Tom Blackledge 6 0


In [87]:
combined_df[combined_df['Event'] == 'UFC 305: Du Plessis vs. Adesanya']


Event                 Date  \
778  UFC 305: Du Plessis vs. Adesanya  2024-08-17 00:00:00   
780  UFC 305: Du Plessis vs. Adesanya  2024-08-17 00:00:00   
805  UFC 305: Du Plessis vs. Adesanya  2024-08-17 00:00:00   
812  UFC 305: Du Plessis vs. Adesanya  2024-08-17 00:00:00   
825  UFC 305: Du Plessis vs. Adesanya  2024-08-17 00:00:00   
827  UFC 305: Du Plessis vs. Adesanya  2024-08-17 00:00:00   
830  UFC 305: Du Plessis vs. Adesanya  2024-08-17 00:00:00   
843  UFC 305: Du Plessis vs. Adesanya  2024-08-17 00:00:00   
863  UFC 305: Du Plessis vs. Adesanya  2024-08-17 00:00:00   
875  UFC 305: Du Plessis vs. Adesanya  2024-08-17 00:00:00   
882  UFC 305: Du Plessis vs. Adesanya  2024-08-17 00:00:00   
900  UFC 305: Du Plessis vs. Adesanya  2024-08-17 00:00:00   

                                Location W/L 1              Fighter 1  \
778  Perth, Western Australia, Australia   win             Song Kenan   
780  Perth, Western Australia, Australia   win              Tom Nolan   
805  Perth, Western Australia, Australia   win           Jack Jenkins   
812  Perth, Western Australia, Australia   win          Casey O'Neill   
825  Perth, Western Australia, Australia   win          Ricardo Ramos   
827  Perth, Western Australia, Australia   win          Valter Walker   
830  Perth, Western Australia, Australia   win          Carlos Prates   
843  Perth, Western Australia, Australia   win  Jairzinho Rozenstruik   
863  Perth, Western Australia, Australia   win             Dan Hooker   
875  Perth, Western Australia, Australia   win        Kai Kara-France   
882  Perth, Western Australia, Australia   win      Dricus Du Plessis   
900  Perth, Western Australia, Australia   win          Jesus Aguilar   

           Fighter 2       Weight class  Stance 1 Career W 1 Career L 1  ...  \
778      Ricky Glenn       Welterweight  Orthodox         20          8  ...   
780       Alex Reyes        Lightweight  Southpaw          7          1  ...   
805    Herbert Burns      Featherweight    Switch         12          3  ...   
812     Luana Santos  Women's Flyweight  Orthodox          9          2  ...   
825     Josh Culibao      Featherweight  Orthodox         16          6  ...   
827      Junior Tafa        Heavyweight  Orthodox         11          1  ...   
830     Li Jingliang       Welterweight    Switch         19          6  ...   
843      Tai Tuivasa        Heavyweight  Orthodox         14          5  ...   
863   Mateusz Gamrot        Lightweight    Switch         23         12  ...   
875      Steve Erceg          Flyweight  Orthodox         24         11  ...   
882  Israel Adesanya       Middleweight    Switch         21          2  ...   
900   Stewart Nicoll          Flyweight  Orthodox         10          2  ...   

    Streak 2 Career W 2 Career L 2 Career Fights 2 Career W Perc 2 Ht Diff 2  \
778       -3         22          8            30.0       73.333333         0   
780       -2         13          4            17.0       76.470588        -4   
805       -3         11          5            16.0           68.75         2   
812        3          8          1             9.0       88.888889         0   
825       -2         11          3            14.0       78.571429         1   
827       -1          5          2             7.0       71.428571        -3   
830       -1         19          8            27.0        70.37037        -1   
843       -4         15          7            22.0       68.181818         0   
863        3         24          2            26.0       92.307692        -2   
875       -1         12          2            14.0       85.714286         4   
882       -1         24          3            27.0       88.888889         3   
900        0          8          0             8.0           100.0         1   

    Reach Diff 2 Age 2  Stance 2 born_year 2  
778           -1    35  Southpaw        1989  
780            0    38  Orthodox        1986  
805            5    36  Orthodox        1988  
812  

In [88]:
combined_df.to_csv("ufc_fights_new_stats_910_2.csv")


In [323]:
len(combined_df)*2


15392

In [324]:
len(all_fights_combined)


15392